In [80]:
# 데이터 프로세서
import csv
records = []
reader = csv.reader( open('result_0606.csv', 'r', encoding = 'utf8', errors = 'ignore'))

col = []
for record in reader:
    records.append(record)
    
data = []
cols = []
for line in records:
    if "_1015" in line[0]:
        data.append(cols[1:])
        cols = []
    cols.append(line)
data.append(cols[1:])
data = data[1:]
print (len(data))

10


In [81]:
import pandas as pd

inputString = []
inputEmotion = []
inputLabel = []
inputDate = []
jj = 0

for ii, topic in enumerate(data):
    if len(topic) != 0:
        jj += 1
    for sent in topic:
        try :
            if float(sent[-1])>=0.2:
                emotion = float(sent[-2])            
                string = ""
                #print(sent[1:-2])
                d = sent[0].split('T')[0]
                #date = d.replace("-","")
                ts = pd.Series(pd.to_datetime(d))        
                date = ts.dt.dayofyear[0]
                for i in sent[1:-2]:
                    string += i
                sentNum = jj-1
            else:
                continue
        except ValueError:
            print(ii)
        
        inputString.append( string )
        inputEmotion.append( emotion )
        inputLabel.append( sentNum )
        inputDate.append(date)

In [3]:
import pandas as pd

inputString = []
inputEmotion = []
inputLabel = []
inputDate = []
jj = 0

for ii, topic in enumerate(data):
    if len(topic) != 0:
        jj += 1
    for sent in topic:
        try :
            if -1.0 <= float(sent[-2]) <-0.25:
                emotion = float(-1)
            elif -0.25 <= float(sent[-2]) < 0.25:
                emotion = float(0)
            else:
                emotion = float(1)
            #emotion = float(sent[-2])            
            string = ""
            #print(sent[1:-2])
            d = sent[0].split('T')[0]
            #date = d.replace("-","")
            ts = pd.Series(pd.to_datetime(d))        
            date = ts.dt.dayofyear[0]
            for i in sent[1:-2]:
                string += i
            sentNum = jj-1
        except ValueError:
            print(ii)
        
        inputString.append( string )
        inputEmotion.append( emotion )
        inputLabel.append( sentNum )
        inputDate.append(date)

In [82]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '1'

%matplotlib inline
import os,random
os.environ["KERAS_BACKEND"] = "theano"
import numpy as np
from keras.utils import np_utils
import keras.models as models
from keras.layers import Input,merge
from keras.layers.core import Reshape,Dense,Dropout,Activation,Flatten
from keras.layers.advanced_activations import LeakyReLU
from keras.activations import *
from keras.layers.wrappers import TimeDistributed
from keras.layers.noise import GaussianNoise
from keras.layers.convolutional import Convolution2D, MaxPooling2D, ZeroPadding2D, Deconv2D, UpSampling2D, Convolution3D, UpSampling3D, MaxPooling3D
from keras.layers.recurrent import LSTM
from keras.regularizers import *
from keras.layers.normalization import *
from keras.optimizers import *
from keras.datasets import mnist
import matplotlib.pyplot as plt
import seaborn as sns
import pickle, random, sys, keras
from keras.models import Model
from IPython import display

sys.path.append("../common")
from keras.utils import np_utils
from tqdm import tqdm

K.set_image_dim_ordering('th')

In [83]:
from collections import Counter, OrderedDict
START = '<start>'
END = '<end>'
UNK = '<unk>'
PAD = '<pad>'

min_count = 2
max_len = 0
train_words_size = 0
vocabulary = Counter()

for inputF in tqdm(inputString):
    caption = inputF
    sent = caption.split()
    vocabulary.update(sent)
    train_words_size += len(sent)
    if len(sent) > max_len: max_len = len(sent)
        
vocabulary = [k for k, v in vocabulary.items() if v >= min_count]
vocabulary = sorted(list(set(vocabulary)))
word_index = OrderedDict()
index_word = OrderedDict()
for index, word in enumerate([START, END, UNK, PAD] + vocabulary):
    word_index[word] = index
    index_word[index] = word
vocabulary_size = len(word_index)

print('vocabulary_size', vocabulary_size)
print('max_len', max_len)
print('train_words_size', train_words_size)

X_lang = []

max_len = max_len+2

for inputF in inputString:
    caption = inputF
    sent = [START] + caption.split() + [END] 
    input_sent = sent[:]
    padding_size = max_len - len(input_sent)

    input_sent = input_sent + padding_size * [PAD]
    input_sent_index = []
    for w in input_sent:
        if w in word_index:
            input_sent_index.append(word_index[w])
        else:
            input_sent_index.append(word_index[UNK])

    X_lang.append(input_sent_index)
    
X_lang = np.array(X_lang)
inputLabel = np.array(inputLabel)
inputEmotion = np.array(inputEmotion)
inputDate = np.array(inputDate)

100%|██████████| 29320/29320 [00:00<00:00, 219344.83it/s]


vocabulary_size 21981
max_len 2013
train_words_size 647039


In [118]:
# Data proprocessing (min-max normalization)
#inputLabel = (inputLabel-np.amin(inputLabel))/(np.amax(inputLabel) - np.amin(inputLabel))
inputEmotion = (inputEmotion-np.amin(inputEmotion))/(np.amax(inputEmotion) - np.amin(inputEmotion))
inputDate = (inputDate-np.amin(inputDate))/(np.amax(inputDate) - np.amin(inputDate))
#X_lang = (X_lang-np.amin(X_lang))/(np.amax(X_lang) - np.amin(X_lang))

In [58]:
# Data preprocessing
inputEmotion -= np.mean(inputEmotion, axis=0) # Mean Subtraction
inputEmotion /= np.std(inputEmotion, axis=0) # Normalization
inputDate -= np.mean(inputDate, axis=0) # Mean Subtraction
inputDate /= np.std(inputDate, axis=0) # Normalization
print (inputEmotion)
print (inputDate)
print (np.std(inputEmotion))
print (np.std(inputDate))

[ 0.12621397  1.15179495  0.38260922 ...,  1.66458543  0.38260922
 -0.38657652]
[ 20  20  20 ..., 123 123 123]
1.0
44.4882766308


In [102]:
# model and input

import numpy as np
np.random.seed(1337)  # for reproducibility

from keras.datasets import mnist
from keras.models import Sequential, load_model
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import SGD, Adam, RMSprop
from keras.utils import np_utils, plot_model

from keras.layers import TimeDistributed, Merge
from keras.layers.wrappers import Bidirectional
from keras.layers.core import RepeatVector
from keras.layers.embeddings import Embedding
from keras.layers import merge

sampleNumber = X_lang.shape[0]
batch_size = 100
nb_classes = 10
nb_epoch = 100

idxs = np.arange(sampleNumber)
np.random.shuffle( idxs )

sample_test =  int(sampleNumber * 0.004);
sample_train = sampleNumber - sample_test;

D_train = inputDate[idxs[sample_test:sampleNumber]]
D_test =  inputDate[idxs[:sample_test]]

E_train = inputEmotion[idxs[sample_test:sampleNumber]]
E_test =  inputEmotion[idxs[:sample_test]]

X_train = X_lang[idxs[sample_test:sampleNumber],:]
X_test =  X_lang[idxs[:sample_test],:]

y_train = inputLabel[idxs[sample_test:sampleNumber]]
y_test  = inputLabel[idxs[:sample_test]]

#X_train = X_train.reshape(50*sample_train, windowSize)
#X_test = X_test.reshape(50*sample_test, windowSize)
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
D_train = D_train.astype('float64')
D_test = D_test.astype('float64')

print(X_train.shape[0], 'train samples')
print(X_test.shape[0], 'test samples')

# convert class vectors to binary class matrices
Y_train = np_utils.to_categorical(y_train, nb_classes)
Y_test = np_utils.to_categorical(y_test, nb_classes)

adam = keras.optimizers.Adam(lr=0.0001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)

29203 train samples
117 test samples


In [ ]:
# 1. Date + Comment, Model

d_input = Input(shape=[1])
g_input = Input(shape=[max_len])
merged_vector = keras.layers.concatenate([d_input, g_input], axis=-1)

GL = Embedding(vocabulary_size, 32)(merged_vector)
GL = Flatten()(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = Dropout(0.8)(GL)
#GL = BatchNormalization(axis=1)(GL)
GL = Dense(10)(GL)
g_V = Activation('softmax')(GL)

model = Model([d_input,g_input], g_V)
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

csv_logger = keras.callbacks.CSVLogger('CD_100.csv')
history = model.fit([D_train, X_train], Y_train,
                    batch_size=batch_size, epochs=nb_epoch,
                    verbose=1, validation_split=0.1, callbacks=[csv_logger])
score = model.evaluate([D_test, X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
input_3 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_4 (InputLayer)             (None, 2015)          0                                            
____________________________________________________________________________________________________
concatenate_2 (Concatenate)      (None, 2016)          0           input_3[0][0]                    
                                                                   input_4[0][0]                    
____________________________________________________________________________________________________
embedding_2 (Embedding)          (None, 2016, 32)      703392      concatenate_2[0][0]     

In [ ]:
# 2. Emotion + Date + Comment, Model

d_input = Input(shape=[1])
e_input = Input(shape=[1])
g_input = Input(shape=[max_len])
merged_vector = keras.layers.concatenate([d_input, e_input, g_input], axis=-1)

GL = Embedding(vocabulary_size, 32)(merged_vector)
GL = Flatten()(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = Dropout(0.8)(GL)
#GL = BatchNormalization(axis=1)(GL)
GL = Dense(10)(GL)
g_V = Activation('softmax')(GL)

model = Model([d_input, e_input, g_input], g_V)
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

csv_logger = keras.callbacks.CSVLogger('result/CDE_100.csv')
history = model.fit( [D_train, E_train, X_train], Y_train,
                    batch_size=batch_size, epochs=nb_epoch,
                    verbose=1, validation_split=0.1, callbacks=[csv_logger])
score = model.evaluate([D_test, E_test, X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
input_8 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_9 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_10 (InputLayer)            (None, 2015)          0                                            
____________________________________________________________________________________________________
concatenate_4 (Concatenate)      (None, 2017)          0           input_8[0][0]                    
                                                                   input_9[0][0]           

In [50]:
# 2. Comment, Model
        
g_input = Input(shape=[max_len])

GL = Embedding(vocabulary_size, 32)(g_input)
GL = Flatten()(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = Dropout(0.8)(GL)
#GL = BatchNormalization(axis=1)(GL)
GL = Dense(10)(GL)
g_V = Activation('softmax')(GL)

csv_logger = keras.callbacks.CSVLogger('C_100.csv')
model = Model([g_input], g_V)
model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
model.summary()

history = model.fit([X_train], Y_train,
                    batch_size=batch_size, epochs=nb_epoch,
                    verbose=1, validation_split=0.1, callbacks=[csv_logger])
score = model.evaluate([X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_11 (InputLayer)        (None, 2015)              0         
_________________________________________________________________
embedding_5 (Embedding)      (None, 2015, 32)          703392    
_________________________________________________________________
flatten_5 (Flatten)          (None, 64480)             0         
_________________________________________________________________
batch_normalization_9 (Batch (None, 64480)             257920    
_________________________________________________________________
dense_13 (Dense)             (None, 100)               6448100   
_________________________________________________________________
activation_13 (Activation)   (None, 100)               0         
_________________________________________________________________
batch_normalization_10 (Batc (None, 100)               400       
__________

In [ ]:
# 2. Comment + Emotion, Model
        
e_input = Input(shape=[1])
g_input = Input(shape=[max_len])

merged_vector = keras.layers.concatenate([e_input, g_input], axis=-1)

GL = Embedding(vocabulary_size, 32)(merged_vector)
GL = Flatten()(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = BatchNormalization(axis=1)(GL)
GL = Dense(100)(GL)
GL = Activation('relu')(GL)
GL = Dropout(0.8)(GL)
#GL = BatchNormalization(axis=1)(GL)
GL = Dense(10)(GL)
g_V = Activation('softmax')(GL)

model = Model([e_input, g_input], g_V)
model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
model.summary()
#plot_model(model, to_file='model.png')

csv_logger = keras.callbacks.CSVLogger('CE_100.csv')
history = model.fit([E_train, X_train], Y_train,
                    batch_size=batch_size, epochs=nb_epoch,
                    verbose=1, validation_data=([E_test, X_test], Y_test), callbacks=[csv_logger])
score = model.evaluate([E_test, X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
input_5 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_6 (InputLayer)             (None, 2015)          0                                            
____________________________________________________________________________________________________
concatenate_3 (Concatenate)      (None, 2016)          0           input_5[0][0]                    
                                                                   input_6[0][0]                    
____________________________________________________________________________________________________
embedding_3 (Embedding)          (None, 2016, 32)      703392      concatenate_3[0][0]     

In [ ]:
csv_logger = keras.callbacks.CSVLogger('CE_100.csv')
history = model.fit([E_train, X_train], Y_train,
                    batch_size=batch_size, epochs=nb_epoch,
                    verbose=1, validation_data=([E_test, X_test], Y_test), callbacks=[csv_logger])
score = model.evaluate([E_test, X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

Train on 26388 samples, validate on 2932 samples
Epoch 1/200
26388/26388 [==============================] - 7s - loss: 0.0314 - acc: 0.9873 - val_loss: 2.7013 - val_acc: 0.6514

In [51]:
model.save('model/C_100.h5')

In [104]:
model = load_model('model/C_100.h5')
#score = model.evaluate([E_test, X_test], Y_test, verbose=0)
score = model.evaluate([X_test], Y_test, verbose=0)

print('Test score:', score[0])
print('Test accuracy:', score[1])

Test score: 1.78282519538
Test accuracy: 0.709401711949


In [105]:
print (X_test)

[[  0.00000000e+00   3.32200000e+03   1.37640000e+04 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]
 [  0.00000000e+00   1.23470000e+04   2.00920000e+04 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]
 [  0.00000000e+00   3.13700000e+03   4.07400000e+03 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]
 ..., 
 [  0.00000000e+00   4.39600000e+03   2.00460000e+04 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]
 [  0.00000000e+00   2.00000000e+00   2.00000000e+00 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]
 [  0.00000000e+00   5.54600000e+03   1.42440000e+04 ...,   3.00000000e+00
    3.00000000e+00   3.00000000e+00]]


In [57]:
from collections import Counter, OrderedDict
START = '<start>'
END = '<end>'
UNK = '<unk>'
PAD = '<pad>'

min_count = 2
max_len = 0
train_words_size = 0
vocabulary = Counter()

for inputF in tqdm(inputString):
    caption = inputF
    sent = caption.split()
    vocabulary.update(sent)
    train_words_size += len(sent)
    if len(sent) > max_len: max_len = len(sent)
        
vocabulary = [k for k, v in vocabulary.items() if v >= min_count]
vocabulary = sorted(list(set(vocabulary)))
word_index = OrderedDict()
index_word = OrderedDict()
for index, word in enumerate([START, END, UNK, PAD] + vocabulary):
    word_index[word] = index
    index_word[index] = word
vocabulary_size = len(word_index)

print('vocabulary_size', vocabulary_size)
print('max_len', max_len)
print('train_words_size', train_words_size)

X_lang = []

max_len = 2015

for inputF in inputString:
    caption = inputF
    sent = [START] + caption.split() + [END] 
    input_sent = sent[:]
    padding_size = max_len - len(input_sent)

    input_sent = input_sent + padding_size * [PAD]
    input_sent_index = []
    for w in input_sent:
        if w in word_index:
            input_sent_index.append(word_index[w])
        else:
            input_sent_index.append(word_index[UNK])

    X_lang.append(input_sent_index)
    
test_lang = np.array(X_lang)
test_Label = np.array(inputLabel)
test_Emotion = np.array(inputEmotion)
test_Date = np.array(inputDate)
Y_test = np_utils.to_categorical(test_Label, nb_classes)

100%|██████████| 84/84 [00:00<00:00, 165486.87it/s]

vocabulary_size 173
max_len 27
train_words_size 1412


In [107]:
sample_test

117

In [73]:
model = load_model('CE_100.h5')
#predict = model.predict([test_Emotion, test_lang], verbose=0)
score = model.evaluate([E_train, test_lang], Y_test, verbose=0)

#print (predict)

print('Test score:', score[0])
print('Test accuracy:', score[1])

Test score: 9.08862495422
Test accuracy: 0.0952380955929


In [72]:
my_df = pd.DataFrame(test_Label)
my_df.to_csv('temp2.csv', index=False, header=False)